In [53]:
import sys
sys.path.append("/home/azhuavlev/PycharmProjects/ml-neuman_mano")

%load_ext autoreload
%autoreload 2

import lighning_models
import lightning as L
from lightning.pytorch.loggers import TensorBoardLogger
import nerf
import dataset_canonical_space
from torch.utils.data import DataLoader
import dataset_from_files
import glob
import os
import glob
import json
import math
import matplotlib.pyplot as plt
import numpy as np
import os
import pytorch3d
import sys
import time
import torch
from IPython import display
from PIL import Image
from pytorch3d.renderer import (
    FoVPerspectiveCameras,
    NDCMultinomialRaysampler,
    MonteCarloRaysampler,
    EmissionAbsorptionRaymarcher,
    ImplicitRenderer,
    RayBundle,
    ray_bundle_to_ray_points,
)
# Data structures and functions for rendering
from pytorch3d.structures import Volumes
from pytorch3d.transforms import so3_exp_map
from tqdm import tqdm

from generate_cow_renders import generate_cow_renders
from plot_image_grid import image_grid

from helpers import *
from nerf import *
import nerf_original

from data_io import neuman_helper

device = 'cuda' if torch.cuda.is_available() else 'cpu'

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [56]:
# disable pytorch gradient computation
torch.set_grad_enabled(False)

data_path = '/home/azhuavlev/Desktop/Data/InterHand_Neuman/03'
all_ids = list(range(len(glob.glob(os.path.join(data_path, 'cameras', '*.json')))))

# use 80% of the data for training, randomize the order
np.random.shuffle(all_ids)
train_ids = all_ids[:int(0.6 * len(all_ids))]
test_ids = all_ids[int(0.6 * len(all_ids)):]
print(test_ids)

train_dataset = dataset_from_files.NeumanDataset(data_path, train_ids)
test_dataset = dataset_from_files.NeumanDataset(data_path, test_ids)
full_dataset = dataset_from_files.NeumanDataset(data_path, all_ids)

# We sample 6 random cameras in a minibatch.
batch_size = 1

train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, num_workers=5)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)
full_loader = DataLoader(full_dataset, batch_size=batch_size, shuffle=False)

field = nerf.NeuralRadianceField()

ckpt_path = '/home/azhuavlev/Desktop/Results/neuman_custom/lightning_logs/version_128/checkpoints/epoch=649-step=23400.ckpt'
model = lighning_models.HandModel(dataset=full_loader, nerf_model=field).load_from_checkpoint(ckpt_path,
                                                                                             dataset=full_loader,
                                                                                             nerf_model=field)

model = model.to('cuda')

[54, 44, 43, 14, 34, 25, 13, 30, 8, 45, 11, 18, 3, 26, 39, 50, 4, 40, 38, 55, 27, 36, 37, 33]
min_depth tensor(0.7476)
max_depth tensor(1.5189)
render_size_x 512
render_size_y 334
min_depth tensor(0.7476)
max_depth tensor(1.5189)
render_size_x 512
render_size_y 334


In [57]:
# generate points in 3d space between -0.3 and 0.3
with torch.no_grad():
    point_cloud = torch.linspace(-0.1, 0.2, 200, device='cpu')
    points = torch.stack(torch.meshgrid(point_cloud, point_cloud, point_cloud), dim=-1).reshape(1, 1, -1, 1, 3)
    directions = torch.zeros(1, 1, points.shape[2], 3, device = points.device)
print('points', points.shape)
print('directions', directions.shape)

points torch.Size([1, 1, 8000000, 1, 3])
directions torch.Size([1, 1, 8000000, 3])


In [58]:
from tqdm import tqdm
# iterate over points in chunks of 1000000:
rays_densities = torch.tensor([], device='cpu')
rays_colors = torch.tensor([], device='cpu')

with torch.no_grad():
    for i in tqdm(range(0, points.shape[2], 1000000)):
        points_batch = points[:, :, i:i+1000000,:,  :].to('cuda')
        directions_batch = directions[:, :, i:i+1000000, :].to('cuda')
        rays_densities_batch, rays_colors_batch = model.get_nerf_output(points_batch, directions_batch)

        rays_densities = torch.cat((rays_densities, rays_densities_batch.cpu()), dim=2)
        rays_colors = torch.cat((rays_colors, rays_colors_batch.cpu()), dim=2)

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 8/8 [00:03<00:00,  2.42it/s]


In [59]:
rays_densities_xyz = rays_densities.reshape(200, 200, 200)

In [60]:
print('fraction occupied > 0.1', np.mean(rays_densities.cpu().numpy() > 0.1))
print('fraction occupied > 0.9', np.mean(rays_densities.cpu().numpy() > 0.9))

fraction occupied > 0.1 0.007346375
fraction occupied > 0.9 0.00132775


In [61]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d.art3d import Poly3DCollection

from skimage import measure
from skimage.draw import ellipsoid
import trimesh

verts, faces, normals, values = measure.marching_cubes(rays_densities_xyz.cpu().numpy(), 0.1)
mesh = trimesh.Trimesh(vertices=verts, faces=faces)

# display mesh
mesh.show()

In [62]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d.art3d import Poly3DCollection

from skimage import measure
from skimage.draw import ellipsoid
import trimesh

verts, faces, normals, values = measure.marching_cubes(rays_densities_xyz.cpu().numpy(), 0.9)
mesh = trimesh.Trimesh(vertices=verts, faces=faces)

# display mesh
mesh.show()

In [63]:
from pytorch3d.structures import Pointclouds
from pytorch3d.vis.plotly_vis import AxisArgs, plot_batch_individually, plot_scene
from pytorch3d.renderer import (
    look_at_view_transform,
    FoVOrthographicCameras,
    PointsRasterizationSettings,
    PointsRenderer,
    PulsarPointsRenderer,
    PointsRasterizer,
    AlphaCompositor,
    NormWeightedCompositor
)

# point_cloud = Pointclouds(points=[points], features=[rays_colors])

In [74]:
# keep the points with opacity > 0.1
points_reshaped = points.reshape(-1, 3)
rays_colors_reshaped = rays_colors.reshape(-1, 3)
rays_densities_reshaped = rays_densities.reshape(-1, 1)

points_reshaped = points_reshaped[rays_densities.reshape(-1) > 0.01]
rays_colors_reshaped = rays_colors_reshaped[rays_densities.reshape(-1) > 0.01]
rays_densities_reshaped = rays_densities_reshaped[rays_densities.reshape(-1) > 0.01]

rays_colors_rgba = np.concatenate((rays_colors_reshaped, rays_densities_reshaped), axis=1)

point_cloud = trimesh.PointCloud(points_reshaped, colors=rays_colors_reshaped)

In [75]:
scene = point_cloud.scene()
scene.show()